In [15]:
import pandas as pd

import rpy2.robjects as ro
from rpy2.robjects import pandas2ri

# R -> pandas
ro.pandas2ri.activate()

# instalacia balika bez warningov
ro.r('''
suppressMessages({
    suppressWarnings({
        if (!require("mlbench")) install.packages("mlbench")
    })
})
''')

# dataset z R-ka, vynechame posledny stlpec (vela NA) a riadky s NA
ro.r("library(mlbench)")
ro.r('options(stringsAsFactors=FALSE)')
ro.r("data('HouseVotes84')")
ro.r("indexy_uplne <- complete.cases(HouseVotes84[, -17])")
ro.r("hlasovanie <- HouseVotes84[indexy_uplne, -17]")
ro.r("hlasovanie[] <- lapply(hlasovanie, function(x) if (is.factor(x)) as.character(x) else x)")

r_votes = ro.r("hlasovanie")

print(type(r_votes))
print(r_votes.head())

<class 'rpy2.robjects.vectors.DataFrame'>
        Class V1 V2 V3 V4 V5 V6 V7 V8 V9 V10 V11 V12 V13 V14 V15
2  republican  n  y  n  y  y  y  n  n  n   n   n   y   y   y   n
6    democrat  n  y  y  n  y  y  n  n  n   n   n   n   y   y   y
9  republican  n  y  n  y  y  y  n  n  n   n   n   y   y   y   n
20   democrat  y  y  y  n  n  n  y  y  y   n   y   n   n   n   y
24   democrat  y  y  y  n  n  n  y  y  y   n   n   n   n   n   y
25   democrat  y  n  y  n  n  n  y  y  y   n   n   n   n   n   y



In [16]:
votes = pandas2ri.rpy2py_dataframe(r_votes)
print(type(votes))
print(votes.head())

<class 'pandas.core.frame.DataFrame'>
         Class V1 V2 V3 V4 V5 V6 V7 V8 V9 V10 V11 V12 V13 V14 V15
2   republican  n  y  n  y  y  y  n  n  n   n   n   y   y   y   n
6     democrat  n  y  y  n  y  y  n  n  n   n   n   n   y   y   y
9   republican  n  y  n  y  y  y  n  n  n   n   n   y   y   y   n
20    democrat  y  y  y  n  n  n  y  y  y   n   y   n   n   n   y
24    democrat  y  y  y  n  n  n  y  y  y   n   n   n   n   n   y


In [17]:
from sklearn.model_selection import train_test_split

votes_train, votes_test  = train_test_split(
    votes,
    test_size=0.2,              # 20% test, 80% train
    stratify=votes["Class"],
    random_state=42
)

print("=== Class ===")
print(votes_train["Class"].value_counts())
print("\n=== Class vs. V1 ===")
print(pd.crosstab(votes_train["Class"], votes_train["V1"]))
print("\n=== Class vs. V8 ===")
print(pd.crosstab(votes_train["Class"], votes_train["V8"]))
print("\n=== Class vs. V15 ===")
print(pd.crosstab(votes_train["Class"], votes_train["V15"]))

=== Class ===
Class
democrat      132
republican     92
Name: count, dtype: int64

=== Class vs. V1 ===
V1           n   y
Class             
democrat    54  78
republican  76  16

=== Class vs. V8 ===
V8           n    y
Class              
democrat    26  106
republican  79   13

=== Class vs. V15 ===
V15          n   y
Class             
democrat    49  83
republican  82  10


In [18]:
print(votes_test.head())

          Class V1 V2 V3 V4 V5 V6 V7 V8 V9 V10 V11 V12 V13 V14 V15
266    democrat  y  n  y  n  n  n  y  y  y   y   n   n   n   n   n
254  republican  n  y  n  y  y  y  n  n  n   n   n   y   y   y   n
255    democrat  y  n  y  n  n  n  y  y  y   y   n   n   n   n   n
341  republican  n  n  n  y  y  y  n  n  n   y   y   y   n   y   n
238    democrat  y  n  y  n  n  y  y  y  n   n   n   y   y   n   n


In [19]:
from sklearn.naive_bayes import CategoricalNB
from sklearn.preprocessing import OrdinalEncoder

# prediktory X a modelovana premenna y
X_train = votes_train[["V1", "V8", "V15"]]
y_train = votes_train["Class"]

X_test = votes_test[["V1", "V8", "V15"]]
y_test = votes_test["Class"]

# transformacia y/n na cisla
encoder = OrdinalEncoder()
X_train_enc = encoder.fit_transform(X_train)
X_test_enc = encoder.transform(X_test)

# naivny Bayesov klasifikator
bayes = CategoricalNB(alpha=0)  # alpha=0 aby to zodpovedalo zakladnemu modelu z prednasky
bayes.fit(X_train_enc, y_train)

# pravdepodobnosti pre testovacie data
predictions_raw = bayes.predict_proba(X_test_enc)
print("Začiatok predikcií v tvare pravdepodobností:")
print(pd.DataFrame(predictions_raw, columns=bayes.classes_).head())

# klasifikacia pre testovacie data
predictions = bayes.predict(X_test_enc)
print("\n")

# porovnanie so skutocnostou
print(pd.crosstab(predictions, y_test, rownames=["Predicted"], colnames=["Actual"]))

Začiatok predikcií v tvare pravdepodobností:
   democrat  republican
0  0.920245    0.079755
1  0.063564    0.936436
2  0.920245    0.079755
3  0.063564    0.936436
4  0.920245    0.079755


Actual      democrat  republican
Predicted                       
democrat          30           4
republican         3          20
